<a href="https://colab.research.google.com/github/adadoun/KplerNextDestination/blob/main/EDA_PortCallsPart1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from datetime import datetime
import plotly.express as px
import plotly.figure_factory as ff

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# Load the port calls and vessels data
df_port_calls = pd.read_csv('drive/MyDrive/Collab_DATA/KplerData/port_calls.csv')
df_vessels = pd.read_csv('drive/MyDrive/Collab_DATA/KplerData/vessels.csv')

In [ ]:
# Rename the 'id' column in the vessels dataframe to 'vessel_id' for clarity
vessels = df_vessels.rename(columns={'id': 'vessel_id'})

# Join the datasets on vessel_id
df_port_calls_with_vessels = pd.merge(df_port_calls, vessels, on='vessel_id', how='left')

# Save the merged dataset to a new CSV file
#df_port_calls_with_vessels.to_csv('../Data/port_calls_with_vessels.csv', index=False)

In [ ]:
# Check the shape of the merged dataset
print(f"\nShape of merged dataset: {df_port_calls_with_vessels.shape}")


Shape of merged dataset: (347277, 16)


## Small Data Transformation before Starting the analysis

In [ ]:
# Convert date columns to datetime
date_columns = ['start_utc', 'end_utc']
for col in date_columns:
    df_port_calls_with_vessels[col] = pd.to_datetime(df_port_calls[col])

# Calculate visit duration in hours
df_port_calls_with_vessels['visit_duration'] = (df_port_calls_with_vessels['end_utc'] - df_port_calls_with_vessels['start_utc']).dt.total_seconds() / 3600  # in hours

## Utilities function

In [ ]:
# Function to remove outliers using IQR method
def remove_outliers(df, column):
    Q1 = df[column].quantile(0.25)
    Q3 = df[column].quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    return df[(df[column] >= lower_bound) & (df[column] <= upper_bound)]

In [ ]:
# Function to set figure size
def set_figure_size(fig, width=800, height=600):
    fig.update_layout(
        width=width,
        height=height
    )
    return fig

## Basic information about the dataset

In [ ]:
# Basic information about the dataset
print(df_port_calls_with_vessels.info())
print("\nMissing values:\n", df_port_calls_with_vessels.isnull().sum())
print("\nUnique values in each column:\n", df_port_calls_with_vessels.nunique())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 347277 entries, 0 to 347276
Data columns (total 17 columns):
 #   Column                 Non-Null Count   Dtype         
---  ------                 --------------   -----         
 0   id                     347277 non-null  int64         
 1   vessel_id              347277 non-null  int64         
 2   start_utc              347277 non-null  datetime64[ns]
 3   end_utc                347253 non-null  datetime64[ns]
 4   cargo_volume           347277 non-null  int64         
 5   draught_change         298006 non-null  float64       
 6   destination            347277 non-null  object        
 7   destination_longitude  346259 non-null  float64       
 8   destination_latitude   346259 non-null  float64       
 9   status                 347277 non-null  object        
 10  status_detail          347277 non-null  object        
 11  build_country          341582 non-null  object        
 12  build_year             347256 non-null  floa

## 1. Port Calls Distribution by Vessel

In [ ]:
# Count the number of port calls per vessel
port_calls_per_vessel = df_port_calls_with_vessels['vessel_id'].value_counts().reset_index()
port_calls_per_vessel.columns = ['vessel_id', 'num_port_calls']

# Calculate statistics
avg_port_calls = port_calls_per_vessel['num_port_calls'].mean()
median_port_calls = port_calls_per_vessel['num_port_calls'].median()
min_port_calls = port_calls_per_vessel['num_port_calls'].min()
max_port_calls = port_calls_per_vessel['num_port_calls'].max()

print(f"Average number of port calls per vessel: {avg_port_calls:.2f}")
print(f"Median number of port calls per vessel: {median_port_calls:.2f}")
print(f"Minimum number of port calls per vessel: {min_port_calls}")
print(f"Maximum number of port calls per vessel: {max_port_calls}")

# Create a violin plot
fig = px.violin(port_calls_per_vessel, y='num_port_calls', box=True, points="all",
                title='Distribution of Port Calls per Vessel')
fig.update_yaxes(title='Number of Port Calls')
fig.update_traces(quartilemethod="exclusive") # Don't include points in box plot whiskers
fig = set_figure_size(fig, width=900, height=600)
fig.show()

# Create a histogram for a different view
fig_hist = px.histogram(port_calls_per_vessel, x='num_port_calls', nbins=300,
                        title='Histogram of Port Calls per Vessel')
fig_hist.update_xaxes(title='Number of Port Calls')
fig_hist.update_yaxes(title='Count of Vessels')
fig_hist = set_figure_size(fig_hist, width=900, height=600)
fig_hist.show()

Average number of port calls per vessel: 39.02
Median number of port calls per vessel: 30.00
Minimum number of port calls per vessel: 1
Maximum number of port calls per vessel: 323


### Comments on the plots:

Port Calls per Vessel:

- The distribution is right-skewed, with most vessels making fewer calls and some making many.
- There's a peak in the 20-40 range for number of port calls per vessel.

## 2. Port Calls Distribution by Vessel

In [ ]:
# Count the number of port calls per destination
port_calls_per_destination = df_port_calls_with_vessels['destination'].value_counts().reset_index()
port_calls_per_destination.columns = ['destination', 'num_port_calls']

# Remove outliers
port_calls_per_destination_no_outliers = remove_outliers(port_calls_per_destination, 'num_port_calls')

# Calculate statistics (after removing outliers)
avg_port_calls = port_calls_per_destination_no_outliers['num_port_calls'].mean()
median_port_calls = port_calls_per_destination_no_outliers['num_port_calls'].median()
min_port_calls = port_calls_per_destination_no_outliers['num_port_calls'].min()
max_port_calls = port_calls_per_destination_no_outliers['num_port_calls'].max()

print(f"Average number of port calls per destination: {avg_port_calls:.2f}")
print(f"Median number of port calls per destination: {median_port_calls:.2f}")
print(f"Minimum number of port calls per destination: {min_port_calls}")
print(f"Maximum number of port calls per destination: {max_port_calls}")

# Create a violin plot
fig = px.violin(port_calls_per_destination_no_outliers, y='num_port_calls', box=True, points="all",
                title='Distribution of Port Calls per Destination (Outliers Removed)')
fig.update_yaxes(title='Number of Port Calls')
fig.update_traces(quartilemethod="exclusive") # Don't include points in box plot whiskers
fig = set_figure_size(fig, width=900, height=600)
fig.show()

# Create a histogram
fig_hist = px.histogram(port_calls_per_destination_no_outliers, x='num_port_calls', nbins=100,
                        title='Histogram of Port Calls per Destination (Outliers Removed)')
fig_hist.update_xaxes(title='Number of Port Calls')
fig_hist.update_yaxes(title='Count of Destinations')
fig_hist = set_figure_size(fig_hist, width=900, height=600)
fig_hist.show()

# Top 10 destinations with most port calls (including outliers for comparison)
top_10_destinations = port_calls_per_destination.nlargest(10, 'num_port_calls')
fig_top10 = px.bar(top_10_destinations, x='destination', y='num_port_calls',
                   title='Top 10 Destinations by Number of Port Calls (Including Outliers)')
fig_top10.update_xaxes(title='Destination')
fig_top10.update_yaxes(title='Number of Port Calls')
fig_top10 = set_figure_size(fig_top10, width=1000, height=500)
fig_top10.show()

# Print information about removed outliers
outliers_removed = len(port_calls_per_destination) - len(port_calls_per_destination_no_outliers)
print(f"\nNumber of outlier destinations removed: {outliers_removed}")
print(f"Percentage of destinations considered outliers: {(outliers_removed / len(port_calls_per_destination)) * 100:.2f}%")

Average number of port calls per destination: 57.52
Median number of port calls per destination: 28.00
Minimum number of port calls per destination: 1
Maximum number of port calls per destination: 317



Number of outlier destinations removed: 266
Percentage of destinations considered outliers: 12.89%


## Comments on the plots:

Port Calls per Destination:

- The distribution is right-skewed, with many destinations receiving few calls and a few receiving many.
- Singapore is the busiest port, followed by Rotterdam and Ulsan.
- There's significant variation in port call frequency across destinations.

## 3. Distribution of Vessel Types

In [ ]:
# Calculate the value counts and percentages
vessel_type_counts = df_port_calls_with_vessels['vessel_type'].value_counts()
vessel_type_percentages = (vessel_type_counts / len(df_port_calls_with_vessels)) * 100

# Create a DataFrame with the percentages
vessel_type_df = pd.DataFrame({
    'vessel_type': vessel_type_percentages.index,
    'percentage': vessel_type_percentages.values
})

# Sort the DataFrame by percentage in descending order
vessel_type_df = vessel_type_df.sort_values('percentage', ascending=False)

# Create the bar plot
fig = px.bar(vessel_type_df, x='vessel_type', y='percentage',
             title='Distribution of Vessel Types (Percentage)')

# Update the axes labels
fig.update_xaxes(title='Vessel Type')
fig.update_yaxes(title='Percentage (%)')

# Format the y-axis to show percentages
fig.update_layout(yaxis_tickformat='.1f')

# Add percentage labels on the bars
fig.update_traces(texttemplate='%{y:.1f}%', textposition='outside')

# Adjust the layout to make room for the labels
fig.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
fig = set_figure_size(fig, width=900, height=600)

# Show the plot
fig.show()


## Comments on the plot:

- Crude Oil Products Tanker is the most common vessel type (42.2%).
- Chemical/Oil Products Tanker (26.2%) and Products Tanker (17.3%) are the next most frequent.
- The dataset primarily covers oil and chemical shipping industry.

## 4. Visit Duration

In [ ]:
# Remove outliers from visit_duration
df_no_outliers = remove_outliers(df_port_calls_with_vessels, 'visit_duration')

# Calculate the percentage of data points removed
percent_removed = (1 - len(df_no_outliers) / len(df_port_calls_with_vessels)) * 100

# Print information about removed outliers
print(f"Number of outliers removed: {len(df_port_calls_with_vessels) - len(df_no_outliers)}")
print(f"Percentage of data points removed: {percent_removed:.2f}%")

# Create the violin plot with outliers removed
fig = px.violin(df_no_outliers, y='visit_duration', box=True, points="all",
                title=f'Distribution of Visit Duration (Outliers Removed, {percent_removed:.2f}% of data removed)')
fig.update_yaxes(title='Visit Duration (hours)')
fig.update_layout(violinmode='overlay')
fig = set_figure_size(fig, width=900, height=600)

# Show the plot
fig.show()

Number of outliers removed: 17204
Percentage of data points removed: 4.95%


## Comments on the plot:¶
- Most port visits last between 10 to 40 hours, with the median around 25 hours.
- There's a concentration of very short visits (less than 10 hours), possibly for quick stops or refueling.
- The distribution has a long tail, indicating some extended stays.

In [ ]:
# Count the number of visits for each destination
visit_counts = df_no_outliers['destination'].value_counts().reset_index()
visit_counts.columns = ['destination', 'visit_count']

# Get the top 20 most visited destinations
top_20_destinations = visit_counts.head(20)['destination'].tolist()

# Calculate average visit duration for these top 20 destinations
avg_duration = df_no_outliers[df_no_outliers['destination'].isin(top_20_destinations)].groupby('destination')['visit_duration'].mean().reset_index()

# Merge with visit counts to get the order
avg_duration = avg_duration.merge(visit_counts, on='destination')

# Sort by visit count (descending) to maintain the order of most visited destinations
avg_duration = avg_duration.sort_values('visit_count', ascending=False)

# Create the bar plot
fig = px.bar(avg_duration, x='destination', y='visit_duration',
             title='Average Visit Duration for Top 20 Most Visited Destinations')
fig.update_xaxes(title='Destination', tickangle=45)
fig.update_yaxes(title='Average Visit Duration (hours)')
fig.update_layout(xaxis_tickmode='linear')  # Ensure all labels are shown
fig.show()